In [1]:
#| include: false

# Imports
import pandas as pd
import pytz
import spacy
import preprocessor as p
from emoji import demojize
from bertopic import BERTopic
import plotly.express as px
import plotly.io as pio
pio.renderers.default = "plotly_mimetype+notebook_connected"

!python -m spacy download es_core_news_sm

/home/fxr/.local/share/virtualenvs/capir_transfronteriza2_2023-f1a4fPBO/lib/python3.8/site-packages/umap/distances.py:1063: NumbaDeprecationWarning: The 'nopython' keyword argument was not supplied to the 'numba.jit' decorator. The implicit default value for this argument is currently False, but it will be changed to True in Numba 0.59.0. See https://numba.readthedocs.io/en/stable/reference/deprecation.html#deprecation-of-object-mode-fall-back-behaviour-when-using-jit for details.
  @numba.jit()
/home/fxr/.local/share/virtualenvs/capir_transfronteriza2_2023-f1a4fPBO/lib/python3.8/site-packages/umap/distances.py:1071: NumbaDeprecationWarning: The 'nopython' keyword argument was not supplied to the 'numba.jit' decorator. The implicit default value for this argument is currently False, but it will be changed to True in Numba 0.59.0. See https://numba.readthedocs.io/en/stable/reference/deprecation.html#deprecation-of-object-mode-fall-back-behaviour-when-using-jit for details.
  @numba.jit(

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 12.9/12.9 MB 4.8 MB/s eta 0:00:00m eta 0:00:010:01:01
✔ Download and installation successful
You can now load the package via spacy.load('es_core_news_sm')


In [2]:
#| include: false

# read data
data = pd.read_csv('../data/processed/tweets.csv')

# replace 'T' from column
data['date'] = data['local_time'].str.replace('T', ' ')

# convert column to datetime and localize to UTC
data['date'] = pd.to_datetime(data['date'], errors='coerce').dt.tz_localize('UTC')

# filter data
df = data[data['user_screen_name'] == 'etorrescobo']

# convert time column to Brasilia, Brazil timezone
df['date'] = df['date'].dt.tz_convert(pytz.timezone('America/Guayaquil'))

print(len(df))

/tmp/ipykernel_46828/685493547.py:4: DtypeWarning:

Columns (6,10,18,19,20,26,28,38,39,40,45,46,47,48,54) have mixed types. Specify dtype option on import or set low_memory=False.



8314


### Datos

Información general sobre la base de datos

In [3]:
min_date = df['date'].min()

max_date = df['date'].max()

print(f"\nPeriodo de tweets recolectados: {min_date} / {max_date}\n")


Periodo de tweets recolectados: 2010-07-06 10:37:00-05:00 / 2023-03-21 09:58:42-05:00



In [4]:
df.info()

<class 'pandas.core.frame.DataFrame'>
Index: 8314 entries, 10617 to 18930
Data columns (total 63 columns):
 #   Column                   Non-Null Count  Dtype                            
---  ------                   --------------  -----                            
 0   query                    8314 non-null   object                           
 1   id                       8314 non-null   float64                          
 2   timestamp_utc            8314 non-null   int64                            
 3   local_time               8314 non-null   object                           
 4   user_screen_name         8314 non-null   object                           
 5   text                     8314 non-null   object                           
 6   possibly_sensitive       2818 non-null   object                           
 7   retweet_count            8314 non-null   float64                          
 8   like_count               8314 non-null   float64                          
 9   reply_co

### Dominios

Lista del top 20 de otros sitios web mencionados en los tweets y su frecuencia

In [5]:
# count items on column
domains_list = df['domains'].value_counts()

# return first n rows in descending order
top_domains = domains_list.nlargest(20)

top_domains

domains
etorrescobo.com             241
tinyurl.com                 141
instagram.com               120
bit.ly                       85
youtu.be                     64
elcomercio.com               64
youtube.com                  52
abc.es                       52
ft.com                       46
eluniverso.com               40
elpais.com                   36
ow.ly                        30
facebook.com                 25
medium.com                   24
expreso.ec                   23
wsj.com                      23
twitter.com                  20
internacional.elpais.com     16
hoy.com.ec                   13
nyti.ms                      12
Name: count, dtype: int64

### Hashtags

Lista del top 20 de hashtags más usados y su frecuencia

In [6]:
# convert dataframe column to list
hashtags = df['hashtags'].to_list()

# remove nan items from list
hashtags = [x for x in hashtags if not pd.isna(x)]

# split items into a list based on a delimiter
hashtags = [x.split('|') for x in hashtags]

# flatten list of lists
hashtags = [item for sublist in hashtags for item in sublist]

# count items on list
hashtags_count = pd.Series(hashtags).value_counts()

# return first n rows in descending order
top_hashtags = hashtags_count.nlargest(20)

top_hashtags

ecuador                   213
ambato                    163
tungurahua                116
quito                      47
venezuela                  43
asambleanacional           35
maduro                     29
trump                      26
españa                     24
vota6                      23
atención                   21
coip                       20
emprendersinobstáculos     19
usfq                       16
colombia                   16
brexit                     15
estebantorres              14
cambio                     14
ecuadorprotesta            14
toros                      13
Name: count, dtype: int64

### Usuarios

Top 20 de usuarios más mencionados en los tweets

In [7]:
# filter column from dataframe
users = df['mentioned_names'].to_list()

# remove nan items from list
users = [x for x in users if not pd.isna(x)]

# split items into a list based on a delimiter
users = [x.split('|') for x in users]

# flatten list of lists
users = [item for sublist in users for item in sublist]

# count items on list
users_count = pd.Series(users).value_counts()

# return first n rows in descending order
top_users = users_count.nlargest(20)

top_users

asambleaecuador    235
estebanperezm      140
etorrescobo        133
lftorrest           86
lassoguillermo      74
bancadapsc          66
eluniversocom       62
rxandrade           57
el_pais             52
usfq_ecuador        48
jfcarpio            47
cambioec            43
abc_es              42
amandahidalgoa      39
xvillalba1          39
ecuavisa            37
cristiano           35
la6ecuador          35
youtube             33
lenin               31
Name: count, dtype: int64

### Likes en el tiempo

In [8]:
# plot the data using plotly
fig = px.line(df, 
              x='date', 
              y='like_count', 
              title='Likes over Time',
              template='plotly_white', 
              hover_data=['text'])

# show the plot
fig.show()

### Tokens

Lista del top 20 de los tokens más comunes y su frecuencia 

In [9]:
# load the spacy model for Spanish
nlp = spacy.load("es_core_news_sm")

# load stop words for Spanish
STOP_WORDS = nlp.Defaults.stop_words

# Function to filter stop words
def filter_stopwords(text):
    # lower text
    doc = nlp(text.lower())
    # filter tokens
    tokens = [token.text for token in doc if not token.is_stop and token.text not in STOP_WORDS and token.is_alpha]
    return ' '.join(tokens)

# apply function to dataframe column
df['text_pre'] = df['text'].apply(filter_stopwords)

# count items on column
token_counts = df["text_pre"].str.split(expand=True).stack().value_counts()[:20]

token_counts

ecuador         586
gracias         388
gobierno        343
vía             332
asamblea        298
saludos         280
país            274
ambato          265
presidente      259
ley             251
artículo        221
nacional        216
the             203
ecuatorianos    178
tungurahua      173
comparto        167
años            161
debate          152
vida            152
quito           150
Name: count, dtype: int64

### Horas

Lista de las 10 horas con más cantidad de tweets publicados

In [10]:
# extract hour from datetime column
df['hour'] = df['date'].dt.strftime('%H')

# count items on column
hours_count = df['hour'].value_counts()

# return first n rows in descending order
top_hours = hours_count.nlargest(10)

top_hours

hour
11    633
10    587
12    578
17    571
20    552
09    503
13    502
21    490
16    469
18    451
Name: count, dtype: int64

### Pataformas

Plataformas desde las que se publicaron contenidos y su frecuencia

In [11]:
df['source_name'].value_counts()

source_name
Twitter for iPhone         4322
Twitter Web Client         1787
Twitter for iPad            704
Twitter for Android         432
Twitter for BlackBerry®     344
Twitter Web App             232
Twitter for Websites        229
Instagram                   105
Kioskoymas                   41
Agorapulse app               33
Mobile Web                   17
Medium                       17
iOS                          14
Hootsuite Inc.               13
TweetChat                     6
Kindle                        5
Canva                         5
FOX News Login                2
Photos on iOS                 2
OS X                          1
Instagram on iOS              1
Crowdfire Inc.                1
bitly bitlink                 1
Name: count, dtype: int64

### Tópicos

Técnica de modelado de tópicos con `transformers` y `TF-IDF`

In [12]:
# remove urls, mentions, hashtags and numbers
p.set_options(p.OPT.URL, p.OPT.MENTION, p.OPT.NUMBER)
df['text_pre'] = df['text_pre'].apply(lambda x: p.clean(x))

# replace emojis with descriptions
df['text_pre'] = df['text_pre'].apply(lambda x: demojize(x))

# filter column
docs = df['text_pre']

# calculate topics and probabilities
topic_model = BERTopic(language="multilingual", calculate_probabilities=True, verbose=True)

# training
topics, probs = topic_model.fit_transform(docs)

# visualize topics
topic_model.visualize_topics()

Batches:   0%|          | 0/260 [00:00<?, ?it/s]

2023-07-21 20:04:20,291 - BERTopic - Transformed documents to Embeddings
2023-07-21 20:04:49,664 - BERTopic - Reduced dimensionality
2023-07-21 20:04:53,932 - BERTopic - Clustered reduced embeddings


### Reducción de tópicos

Mapa con 10 tópicos del contenido de los tweets

In [13]:
# reduce the number of topics
topic_model.reduce_topics(docs, nr_topics=31)

# visualize topics
topic_model.visualize_topics()

2023-07-21 20:06:29,279 - BERTopic - Reduced number of topics from 137 to 31


### Términos por tópico

In [14]:
topic_model.visualize_barchart(top_n_topics=31)

### Análisis de tópicos
Selección de tópicos que tocan temas de género

In [15]:
# selection of topics
topics = [7]

keywords_list = []
for topic_ in topics:
    topic = topic_model.get_topic(topic_)
    keywords = [x[0] for x in topic]
    keywords_list.append(keywords)

# flatten list of lists
words_list = [item for sublist in keywords_list for item in sublist]

# use apply method with lambda function to filter rows
filtered_df = df[df['text_pre'].apply(lambda x: any(word in x for word in words_list))]

percentage = round(100 * len(filtered_df) / len(df), 2)
print(f"Del total de {len(df)} tweets de @etorrescobo, alrededor de {len(filtered_df)} hablan sobre temas de género, es decir, cerca del {percentage}%")

print(f"Lista de palabras en tópicos {topics}:\n{words_list}")

Del total de 8314 tweets de @etorrescobo, alrededor de 542 hablan sobre temas de género, es decir, cerca del 6.52%
Lista de palabras en tópicos [7]:
['aborto', 'mujeres', 'violación', 'matrimonio', 'feminismo', 'despenalización', 'mujer', 'derecho', 'vida', 'coip']


In [16]:
# drop rows with 0 values in two columns
filtered_df = filtered_df[(filtered_df.like_count != 0) & (filtered_df.retweet_count != 0)]

# add a new column with the sum of two columns
filtered_df['impressions'] = (filtered_df['like_count'] + filtered_df['retweet_count'])/2

# extract year from datetime column
filtered_df['year'] = filtered_df['date'].dt.year

# remove urls, mentions, hashtags and numbers
p.set_options(p.OPT.URL)
filtered_df['tweet_text'] = filtered_df['text'].apply(lambda x: p.clean(x))

# Create scatter plot
fig = px.scatter(filtered_df, x='like_count', 
                 y='retweet_count',
                 size='impressions', 
                 color='year',
                 hover_name='tweet_text')

# Update title and axis labels
fig.update_layout(
    title='Tweets talking about gender with most Likes and Retweets',
    xaxis_title='Number of Likes',
    yaxis_title='Number of Retweets'
)

fig.show()

### Tópicos en el tiempo

In [17]:
# convert column to list
tweets = df['text_pre'].to_list()
timestamps = df['local_time'].to_list()

topics_over_time = topic_model.topics_over_time(docs=tweets, 
                                                timestamps=timestamps, 
                                                global_tuning=True, 
                                                evolution_tuning=True, 
                                                nr_bins=20)

topic_model.visualize_topics_over_time(topics_over_time, top_n_topics=20)

20it [00:01, 11.04it/s]
